In [5]:
import sys
sys.path.append('../')
import numpy as np
import pandas as pd
from grid_world.grid_world import GridWorld
from DMEIRL.DeepMEIRL_FC import DMEIRL
from grid_world.trajGen_grid_world import GridWorld_trajGen
from utils import utils

from grid_world.data_parser import DataParser
from grid_world.grid_world import GridWorld


import warnings
warnings.filterwarnings('ignore')

%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [6]:
parser = DataParser(width=10,height=10)
from PIL import Image
import os
from tqdm import tqdm
tracks_path = 'demo_label/train/'
file_names = os.listdir(tracks_path)
#read images
imgs = []
for file_name in file_names:
    imgs.append(Image.open(tracks_path + "/" + file_name))

#parse images
for i in tqdm(range(len(imgs))):
    parser.ParseEnvironment(imgs[i],file_names[i].split('.')[0],save_path='demo_env&feature')

100%|██████████| 4/4 [00:00<00:00, 150.73it/s]


In [7]:
n = np.nan
state_mat = np.array([[ 0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
                       [ 0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
                       [ 0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
                       [ 0, 0, 0, n, n, 0, n, n, n, n],
                       [ 0, 0, 0, n, 0, 0, 0, 0, 0, 0],
                       [ 0, 0, 0, n, 0, 0, 0, 0, 0, 0],
                       [ 0, 0, 0, n, 0, 0, 8, 8, 8, 8],
                       [ 0, 0, 0, n, 0, 0, 8, 8, 8, 8],
                       [ 0, 0, 0, n, 0, 0, 8, 8, 8, 8],
                       [ 0, 0, 0, n, 0, 0, 8, 8, 8, 8],])

world_trajGen = GridWorld_trajGen(10,10,states_matrix=state_mat,
                                  features_folderPath='demo_env&feature/features_grid/0119_10x10',
                                  rewards_mul=[1,-2,-1,-1],
                                  init_states=list(range(0,10)),
                                  trans_prob=0.6,discount=0.9)
world_trajGen.ShowRewards(title='真实奖励')

In [8]:
world_trajGen.GenerateTrajectories(traj_count=500,traj_length=20)

100%|██████████| 500/500 [00:00<00:00, 5345.40it/s]


m                                              trajs
0      1  [(5, 1, 15), (15, 1, 25), (25, 1, 35), (35, 1,...
1      2  [(1, 4, 2), (2, 4, 3), (3, 4, 3), (3, 4, 4), (...
2      3  [(1, 4, 0), (0, 4, 10), (10, 1, 20), (20, 1, 2...
3      4  [(0, 4, 0), (0, 4, 0), (0, 4, 1), (1, 4, 2), (...
4      5  [(2, 4, 3), (3, 4, 4), (4, 4, 5), (5, 1, 15), ...
..   ...                                                ...
495  496  [(0, 4, 0), (0, 4, 1), (1, 4, 1), (1, 4, 1), (...
496  497  [(9, 0, 9), (9, 0, 9), (9, 0, 9), (9, 0, 9), (...
497  498  [(6, 1, 16), (16, 1, 26), (26, 3, 26), (26, 3,...
498  499  [(8, 3, 7), (7, 3, 7), (7, 3, 6), (6, 1, 6), (...
499  500  [(4, 4, 14), (14, 4, 15), (15, 1, 5), (5, 1, 5...

[500 rows x 2 columns]

In [11]:
world_trajGen.ShowTrajs_Experts()

In [10]:
world = GridWorld(
    states_features=world_trajGen.states_features,
    expert_trajs=world_trajGen.df_trajs,
    width=10,
    height=10,
    active_all=False,
    trans_prob=0.6,
    real_reward_mat = world_trajGen.real_rewards_matrix
)
world.ShowGridWorld_Count_log(title='轨迹计数分布(对数)')

In [11]:
world.real_reward_arr.shape

(85,)

In [12]:
world.ShowGridWorld_Activated()

In [13]:
dme = DMEIRL(world,layers = (16,16),lr = 0.001,log='ttttt2',log_dir='test_run')
rewards_result1,rewards1 = dme.train(n_epochs=1000,save = False,demo=True)

100%|██████████| 1000/1000 [48:12<00:00,  2.89s/it]


In [14]:
world.ShowRewardsResult(rewards_result1,title='DMEIRL奖励复原结果')

In [15]:
world.ShowRewardsAnimation(rewards1,title='DMEIRL奖励复原动画')

: 

In [1]:
dme.SaveModel('1_model.pth')

NameError: name 'dme' is not defined